In [1]:
import os; os.chdir('..')

In [2]:
s= '''Ah, spring. It's our season of hope, a time when nature stirs from its winter slumber. The days lengthen, the frost surrenders its grip, and a world once dormant reawakens. The air, once frigid and crisp, transforms, carrying the gentle fragrance of blooming flowers and fresh grass that invigorates the senses. Spring, a time of magic, sees nature's dormant forces burst forth in a vivid spectacle of colors and life.

The trees, once bare, now bud, and delicate green leaves unfurl, creating a lush canopy overhead. Cherry blossoms, daffodils, and tulips paint gardens and parks with their vibrant palettes, infusing the landscape with joy. Birds, returning from their long migrations, fill the air with their'''

In [3]:
import re

def split_sentence(sentence:str):
    # Create a regular expression pattern from the list of separators
    sentence= sentence.replace('\n', '')
    separators = ['. ', '.', ':']
    
    pattern = '|'.join(map(re.escape, separators))

    # Split the sentence using the pattern as a delimiter
    parts = re.split(pattern, sentence)

    return parts

split_sentence(s)


['Ah, spring',
 "It's our season of hope, a time when nature stirs from its winter slumber",
 'The days lengthen, the frost surrenders its grip, and a world once dormant reawakens',
 'The air, once frigid and crisp, transforms, carrying the gentle fragrance of blooming flowers and fresh grass that invigorates the senses',
 "Spring, a time of magic, sees nature's dormant forces burst forth in a vivid spectacle of colors and life",
 'The trees, once bare, now bud, and delicate green leaves unfurl, creating a lush canopy overhead',
 'Cherry blossoms, daffodils, and tulips paint gardens and parks with their vibrant palettes, infusing the landscape with joy',
 'Birds, returning from their long migrations, fill the air with their']

In [4]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("gpt3_finetuned_model/checkpoint-30048")

/home/ubuntu/SentenceStructureComparision/venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [5]:
tokenizer = AutoTokenizer.from_pretrained("gpt2-large")


In [6]:
import numpy as np
def calculate_burst(list_of_sentences):
    arr= []
    for i in list_of_sentences:
        ei= tokenizer(i, return_tensors="pt")
        arr.append(ei.input_ids.size(1))
    print(f"arr= {(arr)}")
    print(f'variance: {np.var(np.array(arr))}')
    print(f'std: {np.std(np.array(arr))}')
    print(f'average length: {np.average(np.array(arr))}')

In [7]:
list_of_sentences= split_sentence(s)
list_of_sentences

['Ah, spring',
 "It's our season of hope, a time when nature stirs from its winter slumber",
 'The days lengthen, the frost surrenders its grip, and a world once dormant reawakens',
 'The air, once frigid and crisp, transforms, carrying the gentle fragrance of blooming flowers and fresh grass that invigorates the senses',
 "Spring, a time of magic, sees nature's dormant forces burst forth in a vivid spectacle of colors and life",
 'The trees, once bare, now bud, and delicate green leaves unfurl, creating a lush canopy overhead',
 'Cherry blossoms, daffodils, and tulips paint gardens and parks with their vibrant palettes, infusing the landscape with joy',
 'Birds, returning from their long migrations, fill the air with their']

In [8]:
calculate_burst(list_of_sentences)

arr= [3, 18, 21, 28, 22, 21, 29, 15]
variance: 58.484375
std: 7.647507763971214
average length: 19.625


# Model Prediction


In [10]:
from transformers import AutoTokenizer
from transformers import AutoModelForSequenceClassification
import torch

tokenizer = AutoTokenizer.from_pretrained("gpt3_finetuned_model/checkpoint-30048")

model = AutoModelForSequenceClassification.from_pretrained("gpt3_finetuned_model/checkpoint-30048")



Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [30]:
from torch.nn import functional as F
def predict(sentence):
    inputs = tokenizer(sentence, return_tensors="pt")
    with torch.no_grad():
        logits = model(**inputs).logits
        
    print("logits: ", logits)
    predicted_class_id = logits.argmax().item()
    # get probabilities using softmax from logit score and convert it to numpy array
    probabilities_scores = F.softmax(logits, dim = -1).numpy()[0]
    print("P(Human): ", probabilities_scores[0])
    print("P(AI): ", probabilities_scores[1])
    label= "Human Written" if model.config.id2label[predicted_class_id]=='NEGATIVE' else 'AI written'
    print("Label: ", label)
    print(model.config.id2label[predicted_class_id])
    



In [31]:
predict('''The Flash (or simply Flash) is the name of several superheroes in the DC Comics universe. Each iteration of the character possesses superhuman speed, allowing them to move at incredible velocities, run on water, phase through solid objects, and even time travel. The most iconic Flash is Barry Allen, who first appeared in 1956 and became the Scarlet Speedster known for his distinctive red costume with a lightning bolt emblem.

Barry Allen's origin story involves a lightning strike combined with a chemical accident, granting him his incredible speed powers. He adopts the superhero persona of The Flash to fight crime in Central City. His adventures often revolve around thwarting supervillains and metahuman threats, while also serving as a founding member of the Justice League.

''')

logits:  tensor([[-7.7618,  7.7867]])
P(Human):  1.7674812e-07
P(AI):  0.9999999
Label:  AI written
POSITIVE


In [32]:
predict(
    '''The Flash first appeared in the Golden Age Flash Comics #1 (January 1940), from All-American Publications, one of three companies that would eventually merge to form DC Comics. Created by writer Gardner Fox and artist Harry Lampert, this Flash was Jay Garrick, a college student who gained his speed through the inhalation of hard water vapors. When re-introduced in the 1960s Garrick's origin was modified slightly, gaining his powers through exposure to heavy water.

Jay Garrick was a popular character in the 1940s, supporting both Flash Comics and All-Flash Quarterly (later published bi-monthly as simply All-Flash); co-starring in Comic Cavalcade; and being a charter member of the Justice Society of America, the first superhero team, whose adventures ran in All Star Comics. With superheroes' post-war decline in popularity, Flash Comics was canceled with issue #104 (1949) which featured an evil version of the Flash called the Rival. The Justice Society's final Golden Age story ran in All Star Comics #57 (1951; the title itself continued as All Star Western).'''
)

logits:  tensor([[ 8.0190, -7.4839]])
P(Human):  0.99999976
P(AI):  1.8500727e-07
Label:  Human Written
NEGATIVE


In [33]:
predict(
    '''Virat Kohli (Hindi pronunciation: [ʋɪˈɾɑːʈ ˈkoːɦli] ⓘ; born 5 November 1988) is an Indian international cricketer and the former captain of the Indian national cricket team who plays for Royal Challengers Bangalore in the IPL and Delhi in domestic cricket. Considered to be one of the best cricketers in the world, he is widely regarded as one of the greatest batsmen in the history of the sport.[4] Nicknamed "The King", due to his dominant style of play and popularity, Kohli holds numerous records in his career across all formats. In 2020, the International Cricket Council named him the male cricketer of the decade. Kohli has also contributed to India's successes, captaining the team from 2014 to 2022, and winning the 2011 World Cup and the 2013 Champions trophy. He is among the only four Indian cricketers who have played over 500 matches for India.[5]

Born and raised in New Delhi, Kohli trained at the West Delhi Cricket Academy and started his youth career with the Delhi Under-15 team. He made his international debut in 2008 and quickly became a key player in the ODI team and later made his Test debut in 2011. In 2013, Kohli reached the number one spot in the ICC rankings for ODI batsmen for the first time. During 2014 T20 World Cup, he set a record for the most runs scored in the tournament. In 2018, he achieved yet another milestone, becoming the world's top-ranked Test batsman, making him the only Indian cricketer to hold the number one spot in all three formats of the game. His form continued in 2019, when he became the first player to score 20,000 international runs in a single decade. In 2021, Kohli made the decision to step down as the captain of the Indian national team for T20Is, following the T20 World Cup and in early 2022 he stepped down as the captain of the Test team as well.'''
)

logits:  tensor([[ 7.9124, -7.3888]])
P(Human):  0.99999976
P(AI):  2.2633e-07
Label:  Human Written
NEGATIVE


In [34]:
predict(
    '''Virat Kohli is an Indian cricketing sensation who has left an indelible mark on the world of sports. Born in Delhi, India, Kohli's journey from a young aspiring cricketer to becoming one of the greatest batsmen in the history of the game is nothing short of remarkable.

Kohli's cricketing prowess was evident from a tender age, and he quickly rose through the ranks of junior cricket in India. He made his debut for the Indian national team in 2008, and since then, he has been a symbol of consistency and excellence. His distinctive blend of aggression and technical finesse at the crease has earned him a reputation as a modern-day batting maestro.'''
)

logits:  tensor([[-8.4224,  8.2709]])
P(Human):  5.6263374e-08
P(AI):  1.0
Label:  AI written
POSITIVE
